In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import numpy as np
import os

In [3]:
from cellpose_omni import models, core
from cellpose_omni import plot

2023-02-06 17:17:00,291 [INFO] No OpenGL_accelerate module loaded: No module named 'OpenGL_accelerate'


In [4]:
import omnipose
from cellpose_omni import models
from glob import glob
from natsort import natsorted

In [5]:

# This checks to see if you have set up your GPU properly.
# CPU performance is a lot slower, but not a problem if you
# are only processing a few images.
use_GPU = core.use_gpu()
print('>>> GPU activated? %d'%use_GPU)

import tifffile
from skimage.transform import rescale, resize, downscale_local_mean

# for plotting
import matplotlib as mpl
import matplotlib.pyplot as plt

2023-02-06 17:17:01,580 [INFO] ** TORCH GPU version installed and working. **
>>> GPU activated? 1


In [6]:
from PIL import Image

In [7]:
test_data_dir = "omnipose_SyMBac_TD_fl/20x blur/"
mask = sorted(glob(test_data_dir + "masks/*"))
conv = sorted(glob(test_data_dir + "convolutions/*"))
masks = [np.asarray(Image.open(file)) for file in mask]
convs = [np.asarray(Image.open(file)) for file in conv]

In [8]:
from cellpose_omni import io, transforms
from omnipose.utils import normalize99
imgs = convs
nimg = len(imgs)
fig = plt.figure(figsize=[16,12]) # initialize figure
for k in range(len(imgs)):
    print(imgs[k].shape)
    img = transforms.move_min_dim(imgs[k]) # move the channel dimension last
    if len(img.shape)>2:
        imgs[k] = np.mean(img,axis=-1) # or just turn into grayscale

    imgs[k] = normalize99(imgs[k])
    plt.subplot(1,len(imgs),k+1)
    plt.imshow(imgs[k],cmap='gray')
    plt.axis('off')

(19, 200)
(19, 200)
(19, 200)
(19, 200)
(19, 200)
(19, 200)
(19, 200)
(19, 200)
(19, 200)
(19, 200)


In [9]:
model_list = natsorted(glob("C:/Users/robho/OneDrive/Desktop/Uni Work/Year 4/project2/omnipose_SyMBac_TD_fl/20x/models/*"))
model_name = model_list[-1]
print(type(model_name), model_name)
use_gpu = use_GPU# = False
model = models.CellposeModel(gpu=use_gpu, pretrained_model=model_name, omni=True,concatenation=True)

<class 'str'> C:/Users/robho/OneDrive/Desktop/Uni Work/Year 4/project2/omnipose_SyMBac_TD_fl/20x/models\cellpose_residual_on_style_on_concatenation_off_omni_nclasses_4_20x_2023_01_24_13_21_12.858051_epoch_499
2023-02-06 17:17:02,733 [INFO] ** TORCH GPU version installed and working. **
2023-02-06 17:17:02,734 [INFO] >>>> using GPU
type <class 'cellpose_omni.resnet_torch.CPnet'>
OrderedDict([('downsample.down.res_down_0.conv.conv_0.0.weight', tensor([7.4980, 0.5211], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.bias', tensor([ 1.8916, -0.4701], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.running_mean', tensor([0.0687, 0.6323], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.running_var', tensor([0.0476, 0.2325], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.num_batches_tracked', tensor(6500, device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.2.weight', tensor([[[[ 3.6040e+00, -4.2946e+00, -5.8017e+00],
          [

In [10]:
chans = [0,0] #this means segment based on first channel, no second channel

n = [0] # make a list of integers to select which images you want to segment
n = range(nimg) # or just segment them all

# define parameters
mask_threshold = -1
verbose = 0 # turn on if you want to see more output
use_gpu = use_GPU #defined above
transparency = True # transparency in flow output
rescale=None # give this a number if you need to upscale or downscale your images
omni = True # we can turn off Omnipose mask reconstruction, not advised
flow_threshold = 0. # default is .4, but only needed if there are spurious masks to clean up; slows down output
resample = True #whether or not to run dynamics on rescaled grid or original grid
masks, flows, styles = model.eval([imgs[i] for i in n],channels=chans,rescale=rescale,mask_threshold=mask_threshold,transparency=transparency,
                                  flow_threshold=flow_threshold,omni=omni,resample=resample,verbose=verbose)

2023-02-06 17:17:05,942 [INFO] 0%|          | 0/10 [00:00<?, ?it/s]
OrderedDict([('downsample.down.res_down_0.conv.conv_0.0.weight', tensor([7.4980, 0.5211], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.bias', tensor([ 1.8916, -0.4701], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.running_mean', tensor([0.0687, 0.6323], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.running_var', tensor([0.0476, 0.2325], device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.0.num_batches_tracked', tensor(6500, device='cuda:0')), ('downsample.down.res_down_0.conv.conv_0.2.weight', tensor([[[[ 3.6040e+00, -4.2946e+00, -5.8017e+00],
          [ 7.5415e-01, -2.5390e+00, -3.2102e-01],
          [ 1.9917e+00,  1.4556e+00,  2.2407e+00]],

         [[ 3.4146e-02,  5.9541e-02,  5.8437e-02],
          [-5.7801e-03, -3.1374e-02, -2.1401e-01],
          [-1.6917e-03, -4.6989e-02, -5.4056e-02]]],


        [[[-4.9447e-01, -3.6500e+00, -4.1230e-01],
          [-

In [11]:
os.mkdir(f"{test_data_dir}omnipose segmentations")
for idx,i in enumerate(n):

    maski = masks[idx]
    flowi = flows[idx][0]
    im = Image.fromarray(maski)
    im.save(f"{test_data_dir}omnipose segmentations/mask_{str(idx).zfill(5)}.png")
    
    # fig = plt.figure(figsize=(10,12))
    # plot.show_segmentation(fig, omnipose.utils.normalize99(imgs[i]), maski, flowi, channels=chans, omni=True, bg_color=0)

    # plt.tight_layout()
    # plt.savefig(f"fluo/60x test/omnipose images/{str(idx).zfill(4)}.png", dpi = 120)
    # plt.show()

In [85]:
import torch
print(torch.cuda.is_available())
torch.zeros(1).cuda()

True


tensor([0.], device='cuda:0')